# Looking at the Dataset
The purpose of this notebook is to look closer at the dataset of genes, natural language descriptions, and ontology term annotations that are used in this work. As included in the preprocessing notebooks, these data are drawn from files from either publications supplements like Oellrich, Walls et al. (2015) or model species databases such as TAIR, MaizeGDB, and SGN. The datasets are already loaded and merged using classe available through the oats package.

In [13]:
import datetime
import nltk
import pandas as pd
import numpy as np
import time
import math
import sys
import gensim
import os
import warnings
from collections import defaultdict
from nltk.corpus import brown
from nltk.tokenize import word_tokenize, sent_tokenize
from gensim.parsing.preprocessing import strip_non_alphanum, stem_text, preprocess_string, remove_stopwords
from gensim.utils import simple_preprocess
from nltk.stem import WordNetLemmatizer
from nltk.tokenize import word_tokenize

sys.path.append("../../oats")
from oats.utils.utils import save_to_pickle, load_from_pickle, merge_list_dicts, flatten, to_hms
from oats.biology.dataset import Dataset
from oats.biology.groupings import Groupings
from oats.biology.relationships import ProteinInteractions, AnyInteractions
from oats.annotation.ontology import Ontology

warnings.simplefilter('ignore')
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
pd.set_option('display.width', 1000)
nltk.download('punkt', quiet=True)
nltk.download('brown', quiet=True)
nltk.download('averaged_perceptron_tagger', quiet=True)

True

In [2]:
data = load_from_pickle("../data/pickles/gene_phenotype_dataset_all_text_and_annotations_unmerged.pickle")
data.to_pandas().head()
data.describe()

species  num_genes  unique_descriptions
0     ath     628658                 9110
1     gmx        156                   49
2     mtr        342                  155
3     osa        772                  389
4     sly        786                  314
5     zma       6526                  998
6   total     637240                11015

In [3]:
data = load_from_pickle("../data/pickles/gene_phenotype_dataset_all_text_and_annotations.pickle")
data.filter_has_description()
data.to_pandas().head()
data.describe()

species  num_genes  unique_descriptions
0     ath       6364                 3813
1     gmx         30                   24
2     mtr         37                   36
3     osa         92                   85
4     sly         70                   70
5     zma       1406                  811
6   total       7999                 4839

### What's there for each species?
The previously loaded dataset contains all of the genes that across six plant species that have natural language description data for phenotype(s) related to that gene. Each gene can have multiple descriptions annotated to it, which were combined or concatenated when the datasets from multiple sources were merged in creating the pickled datasets. Arabidopsis has the highest number of genes that satisfy this criteria, followed by maize, and then followed by the other four species which have a relatively low number of genes that satisfy this criteria, atleast given the sources used for this work. Note that the number of unique descriptions is lower than the number of genes in call cases, because multiple genes can have the same phenotype description associated with them.

In [4]:
wnl = WordNetLemmatizer()
lemmatize_doc = lambda d: [wnl.lemmatize(x) for x in simple_preprocess(d)]


token_lists = {}
stems_lists = {}
lemma_lists = {}

# For each individual species.
for species in data.get_species():
    df = data.to_pandas()
    subset = df[df["species"]==species]
    descriptions_not_stemmed = [simple_preprocess(d) for d in subset["description"].values]
    descriptions_stemmed = [preprocess_string(d) for d in subset["description"].values]
    descriptions_lemmatized = [lemmatize_doc(d) for d in subset["description"].values]
    token_lists[species] = flatten(descriptions_not_stemmed)
    stems_lists[species] = flatten(descriptions_stemmed)    
    lemma_lists[species] = flatten(descriptions_lemmatized)
    
    po = len([t for t in subset["term_ids"].values if "PO" in t])
    go = len([t for t in subset["term_ids"].values if "GO" in t])
    
# For the entire dataset including all of the species.
df = data.to_pandas()
subset = df
descriptions_not_stemmed = [simple_preprocess(d) for d in subset["description"].values]
descriptions_stemmed = [preprocess_string(d) for d in subset["description"].values]
token_lists["total"] = flatten(descriptions_not_stemmed)
stems_lists["total"] = flatten(descriptions_stemmed)    
    
df = data.describe() 
df["total_words"] = df["species"].map(lambda x: len(token_lists[x]))
df["unique_words"] = df["species"].map(lambda x: len(set(token_lists[x])))
df["unique_stems"] = df["species"].map(lambda x: len(set(stems_lists[x])))
df

species  num_genes  unique_descriptions  total_words  unique_words  unique_stems
0     ath       6364                 3813       264189          7085          5116
1     gmx         30                   24          233            81            68
2     mtr         37                   36         2672           718           516
3     osa         92                   85         3887           826           586
4     sly         70                   70         1810           577           438
5     zma       1406                  811        50029          1846          1317
6   total       7999                 4839       322820          8043          5802

### What about the ontology term annations for each species?

In [5]:
# How many of the genes in this dataset for each species are mapped to atleast one term from a given ontology?
num_mapped_go = {}
num_mapped_po = {}
for species in data.get_species():
    d = data.to_pandas()
    subset = d[d["species"]==species]    
    num_mapped_po[species] = len([t for t in subset["term_ids"].values if "PO" in t])
    num_mapped_go[species] = len([t for t in subset["term_ids"].values if "GO" in t])
num_mapped_go["total"] = sum(list(num_mapped_go.values()))   
num_mapped_po["total"] = sum(list(num_mapped_po.values()))
df["go"] = df["species"].map(lambda x: num_mapped_go[x])
df["po"] = df["species"].map(lambda x: num_mapped_po[x])
df

species  num_genes  unique_descriptions  total_words  unique_words  unique_stems    go    po
0     ath       6364                 3813       264189          7085          5116  5434  4420
1     gmx         30                   24          233            81            68    28    27
2     mtr         37                   36         2672           718           516    30    32
3     osa         92                   85         3887           826           586    46    92
4     sly         70                   70         1810           577           438    23    65
5     zma       1406                  811        50029          1846          1317   184   111
6   total       7999                 4839       322820          8043          5802  5745  4747

### What about the biologically relevant groups like biochemical pathways and phenotypes?

In [6]:
# What are the groupings that we're interested in mapping to?
kegg_pathways_filename = "../data/pickles/groupings_from_kegg_pathways.pickle" 
pmn_pathways_filename = "../data/pickles/groupings_from_pmn_pathways.pickle"                        
lloyd_subsets_filename = "../data/pickles/groupings_from_lloyd_subsets.pickle"                     
groupings_dict = {"kegg":kegg_pathways_filename,"plantcyc":pmn_pathways_filename,"lloyd":lloyd_subsets_filename}

for name,filename in groupings_dict.items():
    groups = load_from_pickle(filename)
    id_to_group_ids, group_id_to_ids = groups.get_groupings_for_dataset(data)
    group_mapped_ids = [k for (k,v) in id_to_group_ids.items() if len(v)>0]
    species_dict = data.get_species_dictionary()
    num_mapped = {}
    for species in data.get_species():
        inputt = len([x for x in data.get_ids() if species_dict[x]==species]) 
        num_mapped[species] = len([x for x in group_mapped_ids if species_dict[x]==species])
    num_mapped["total"] = sum(list(num_mapped.values()))    
    df[name] = df["species"].map(lambda x: num_mapped[x])  
df.to_csv("~/Desktop/a.csv")
df


species  num_genes  unique_descriptions  total_words  unique_words  unique_stems    go    po  kegg  plantcyc  lloyd
0     ath       6364                 3813       264189          7085          5116  5434  4420  1572       926   2868
1     gmx         30                   24          233            81            68    28    27     1         0      0
2     mtr         37                   36         2672           718           516    30    32     0         2      0
3     osa         92                   85         3887           826           586    46    92     0         3      0
4     sly         70                   70         1810           577           438    23    65    17         2      0
5     zma       1406                  811        50029          1846          1317   184   111   156       133      0
6   total       7999                 4839       322820          8043          5802  5745  4747  1746      1066   2868

### How do the vocabularies used for different species compare?
One of the things we are interested in is discovering or recovering phenotype similarity between different species in order to identify phenologs (phenotypes between species that share some underlying genetic cause). For this reason, we are interested in how the vocabularies used to describe phenotypes between different species vary, because this will impact how feasible it is to use a dataset like this to identify phenologs. Because the Arabidopsis and maize datasets are the largest in this case, we will compare the vocabularies used in describing the phenotypes associated with the genes from these species in this dataset.

In [7]:
import nltk
from nltk.corpus import stopwords
from nltk.probability import FreqDist

vocabs = {s:set(lemma_list) for s,lemma_list in lemma_lists.items()}
fdist_zma = FreqDist(lemma_lists["zma"])
fdist_ath = FreqDist(lemma_lists["ath"])

#vocabs = {s:set(stems_list) for s,stems_list in stems_lists.items()}
#fdist_zma = FreqDist(stems_lists["zma"])
#fdist_ath = FreqDist(stems_lists["ath"])

#vocabs = {s:set(token_list) for s,token_list in token_lists.items()}
#fdist_zma = FreqDist(token_lists["zma"])
#fdist_ath = FreqDist(token_lists["ath"])


union_vocab = vocabs["zma"].union(vocabs["ath"])
table = pd.DataFrame({"token":list(union_vocab)})
stops = set(stopwords.words('english'))
table = table[~table.token.isin(stops)]
table["part_of_speech"] = table["token"].map(lambda x: nltk.pos_tag([x])[0][1][:2])
table["ath_freq"] = table["token"].map(lambda x: fdist_ath[x])
table["ath_rate"] = table["ath_freq"]*100/len(token_lists["ath"])
table["zma_freq"] = table["token"].map(lambda x: fdist_zma[x])
table["zma_rate"] = table["zma_freq"]*100/len(token_lists["zma"])
table["diff"] = table["ath_rate"]-table["zma_rate"]
table.to_csv("~/Desktop/a.csv")
table.head()

token part_of_speech  ath_freq  ath_rate  zma_freq  zma_rate      diff
0     sitosterol             NN         2  0.000757         0       0.0  0.000757
1      hypomorph             NN         1  0.000379         0       0.0  0.000379
2            nyc             NN         1  0.000379         0       0.0  0.000379
3  organogenesis             NN         5  0.001893         0       0.0  0.001893
4  fluorouridine             NN         4  0.001514         0       0.0  0.001514

In [8]:
# What are the tokens more frequently used for Arabidopsis than maize?
table.sort_values(by="diff", ascending=False, inplace=True)
table.head(30)

token part_of_speech  ath_freq  ath_rate  zma_freq  zma_rate      diff
6581       embryo             NN      4995  1.890692       151  0.301825  1.588867
4128       mutant             NN      4778  1.808554       256  0.511703  1.296851
5490    phenotype             NN      3583  1.356226        78  0.155910  1.200316
3715         root             NN      2943  1.113975        72  0.143917  0.970059
271          type             NN      2540  0.961433        15  0.029983  0.931450
3978         wild             NN      2456  0.929637         7  0.013992  0.915646
479     defective             JJ      3341  1.264625       285  0.569670  0.694955
4435      reduced             VB      2860  1.082558       216  0.431750  0.650809
7035        stage             NN      1814  0.686630        63  0.125927  0.560703
5916    cotyledon             NN      1443  0.546200         0  0.000000  0.546200
28         growth             NN      1830  0.692686        79  0.157908  0.534778
1707         seed             NN      1890  0.715397       113  0.225869  0.489528
3875    increased             VB      1316  0.498128        11  0.021987  0.476141
2236     terminal             NN      1268  0.479959         4  0.007995  0.471964
2013        level             NN      1336  0.505699        22  0.043974  0.461724
939          cell             NN      1646  0.623039       112  0.223870  0.399169
583       rosette             NN       967  0.366026         1  0.001999  0.364027
1306       double             RB       956  0.361862         3  0.005997  0.355866
526      globular             NN       905  0.342558         0  0.000000  0.342558
1324     abnormal             JJ      1049  0.397064        28  0.055968  0.341097
849            wa             NN       886  0.335366         1  0.001999  0.333367
5885       flower             NN       940  0.355806        14  0.027984  0.327822
4241    flowering             VB      1031  0.390251        32  0.063963  0.326288
2222        short             JJ      1504  0.569289       123  0.245857  0.323432
1350     compared             VB       882  0.333852         9  0.017990  0.315862
1058      silique             NN       798  0.302056         0  0.000000  0.302056
5453    sensitive             JJ       827  0.313033         6  0.011993  0.301040
617       visible             JJ       838  0.317197        13  0.025985  0.291212
3645  development             NN       862  0.326282        19  0.037978  0.288304
2507    hypocotyl             NN       752  0.284645         0  0.000000  0.284645

In [9]:
# What are the tokens more frequently used for maize than Arabidopsis?
table.sort_values(by="diff", ascending=True, inplace=True)
table.head(30)

token part_of_speech  ath_freq  ath_rate  zma_freq  zma_rate      diff
5393   endosperm             NN       124  0.046936      1078  2.154750 -2.107814
3545    seedling             VB      1560  0.590486      1318  2.634472 -2.043986
4727      kernel             NN         0  0.000000       766  1.531112 -1.531112
1426      yellow             NN       304  0.115069       775  1.549102 -1.434032
608         leaf             NN      3879  1.468267      1445  2.888325 -1.420058
816        green             JJ       884  0.334609       788  1.575086 -1.240478
501        white             JJ       375  0.141944       642  1.283256 -1.141312
4430      albino             NN       222  0.084031       396  0.791541 -0.707510
865      usually             RB        46  0.017412       353  0.705591 -0.688179
2765       color             NN        43  0.016276       330  0.659617 -0.643341
5899      tassel             NN         0  0.000000       310  0.619641 -0.619641
2071         ear             NN         0  0.000000       284  0.567671 -0.567671
4347       often             RB       149  0.056399       278  0.555678 -0.499279
2685    aleurone             NN         3  0.001136       248  0.495712 -0.494577
3794      opaque             NN         1  0.000379       244  0.487717 -0.487339
2261       class             NN         8  0.003028       240  0.479722 -0.476694
3158      tissue             NN       236  0.089330       259  0.517700 -0.428370
4986       small             JJ       670  0.253606       323  0.645626 -0.392019
3557        pale             NN       651  0.246414       318  0.635631 -0.389217
606           vp             NN         0  0.000000       190  0.379780 -0.379780
3164   palegreen             NN         1  0.000379       171  0.341802 -0.341423
4033     general             JJ        13  0.004921       171  0.341802 -0.336881
896         term             NN        22  0.008327       172  0.343801 -0.335473
2899     surface             NN       138  0.052235       190  0.379780 -0.327544
5948  appearance             NN       131  0.049586       188  0.375782 -0.326196
4188     texture             NN         2  0.000757       163  0.325811 -0.325054
480    otherwise             RB        10  0.003785       158  0.315817 -0.312032
5945      anther             NN       139  0.052614       167  0.333806 -0.281193
3213    pericarp             NN         0  0.000000       140  0.279838 -0.279838
593    sometimes             RB        44  0.016655       148  0.295828 -0.279174

In [10]:
# Is the mean absolute value of the rate differences different between the different parts of speech?
table["abs_diff"] = abs(table["diff"])
pos_table = table.groupby("part_of_speech").mean()
pos_table.sort_values(by="abs_diff", inplace=True, ascending=False)
pos_table = pos_table[["abs_diff"]]
pos_table.reset_index()

part_of_speech  abs_diff
0             MD  0.059430
1             CD  0.027894
2             IN  0.026202
3             JJ  0.023688
4             DT  0.019077
5             RB  0.016302
6             NN  0.014463
7             VB  0.012131
8             CC  0.007617
9             WP  0.001620

In [11]:
print(table.shape)
zma_only = table[table["ath_rate"]==0]
ath_only = table[table["zma_rate"]==0]
print(zma_only.shape)
print(ath_only.shape)
print(ath_only.shape[0]+zma_only.shape[0])
ath_only.head(10)


# We need to create a mapping between stems and the words that were present for them.
# This is because what we want is the stems that are exclusive to a species.
# but then the words that are actually there for those stems, so that we can count their parts of speech.



(7000, 8)
(540, 8)
(5352, 8)
5892


token part_of_speech  ath_freq  ath_rate  zma_freq  zma_rate      diff  abs_diff
6960      possessing             VB         1  0.000379         0       0.0  0.000379  0.000379
172       salicylide             NN         1  0.000379         0       0.0  0.000379  0.000379
170   ribonucleotide             NN         1  0.000379         0       0.0  0.000379  0.000379
164             ppck             NN         1  0.000379         0       0.0  0.000379  0.000379
6966       leptotene             NN         1  0.000379         0       0.0  0.000379  0.000379
163         slanting             VB         1  0.000379         0       0.0  0.000379  0.000379
160            salty             NN         1  0.000379         0       0.0  0.000379  0.000379
6718           atarp             NN         1  0.000379         0       0.0  0.000379  0.000379
167   mophologically             RB         1  0.000379         0       0.0  0.000379  0.000379
6959             adn             NN         1  0.000379         0       0.0  0.000379  0.000379

In [22]:
lemmas = []
lemmas.extend([wnl.lemmatize(x) for x in Ontology("../ontologies/po.obo").get_tokens()])
lemmas.extend([wnl.lemmatize(x) for x in Ontology("../ontologies/go.obo").get_tokens()])
print(len(lemmas))

RecursionError: maximum recursion depth exceeded while calling a Python object

In [23]:
ont = Ontology("../ontologies/go.obo")
print("done")

RecursionError: maximum recursion depth exceeded while calling a Python object